## 💼 Análise: Ranking dos Clientes Mais Lucrativos

Este relatório apresenta um ranking dos 10 clientes que mais contribuíram para a receita da empresa, com base na tabela de fatos `fato_vendas` integrada à dimensão `dim_cliente`.

---

### 📊 Objetivo

Identificar os clientes mais lucrativos com base no total de compras (`ReceitaTotal`), possibilitando:

- **Campanhas de fidelização** direcionadas
- **Ações de retenção** para os melhores clientes
- **Priorização no atendimento comercial**

### ✅ Benefícios para o Negócio

- **Visão estratégica** dos clientes com maior valor financeiro
- Suporte à criação de **programas de relacionamento**
- Insights para **ações comerciais personalizadas**

In [0]:
from pyspark.sql.functions import col, sum, desc, row_number, round
from pyspark.sql.window import Window

# 📁 Caminhos das tabelas Delta na camada Gold
FATO_VENDAS_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_fato_vendas"
DIM_CLIENTE_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_dim_cliente"

# 📥 Leitura das tabelas fato e dimensão
df_fato_vendas = spark.read.format("delta").load(FATO_VENDAS_PATH)
df_dim_cliente = spark.read.format("delta").load(DIM_CLIENTE_PATH)

# 📊 Agregação de receita total por cliente
df_receita_por_cliente = (
    df_fato_vendas.groupBy("CustomerID")
    .agg(round(sum("TotalAmount"), 2).alias("ReceitaTotal"))  # 🎯 Arredonda para 2 casas
)

# 🔗 Junção com a dimensão cliente
df_join = (
    df_receita_por_cliente.join(df_dim_cliente, on="CustomerID", how="inner")
)

# Define uma janela de ordenação (Window Specification) que classifica os clientes com base na receita total.
# Esta especificação será usada com funções de janela (como row_number()) para calcular rankings sem agregações 
windowSpec = Window.orderBy(desc("ReceitaTotal"))

# 🏆 Ranking + seleção final
df_ranking = (
    df_join.select(
        "CustomerID", "Name", "City", "State", "Country", "ReceitaTotal"
    )
    .dropDuplicates(["CustomerID"])  # ✅ Garante cliente único
    .withColumn("Rank", row_number().over(windowSpec))  # 🏅 Ranking decrescente
    .orderBy("Rank")
)

# 🔝 Top 10 clientes mais lucrativos
df_ranking.filter(col("Rank") <= 10).display()


CustomerID Name City State Country ReceitaTotal Rank 397 Dennis Spears Lake Johnnymouth WI Brazil 170942.34 1 17 Gloria Mills West Michael RI Tonga 167369.37 2 369 Alexa Rodriguez Port Geraldberg ID Italy 166223.79 3 243 Chelsey Bauer Clarkberg HI Faroe Islands 158942.97 4 174 Lindsey Miller Ellistown AL Belarus 157323.51 5 208 Allison Gutierrez Allenland MN San Marino 156296.13 6 320 Krystal Williams Jessicatown WY Palestinian Territory 146044.98 7 182 Dr. Lee Lowery DDS East Dustin MD United Kingdom 143962.38 8 334 Ronald Edwards Lake Alyssachester IA Malta 143958.66 9 291 Kayla Campbell Lake Jenniferside WY French Southern Territories 143074.41 10

# 📍 Análise de Regiões com Maior Volume de Vendas

## 🎯 Objetivo

Esta análise tem como objetivo identificar as **regiões (Estados e Países)** com maior volume de vendas, com base nos dados da tabela de fatos `fato_vendas` e da dimensão `dim_cliente`.

Com este insight, a empresa pode:

- Otimizar estratégias **logísticas e operacionais**
- Direcionar **esforços de marketing e vendas** para as regiões mais lucrativas
- Avaliar oportunidades de **expansão geográfica**

## 📊 Benefícios da Análise

- Melhora a **alocação de recursos comerciais**
- Ajuda na **definição de metas regionais**
- Suporte para **decisões de expansão territorial**

In [0]:
from pyspark.sql.functions import col, sum, round, desc

# 📁 Caminhos das tabelas Delta na camada Gold
FATO_VENDAS_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_fato_vendas"
DIM_CLIENTE_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_dim_cliente"

# 📥 Leitura das tabelas fato e dimensão
df_fato_vendas = spark.read.format("delta").load(FATO_VENDAS_PATH)
df_dim_cliente = spark.read.format("delta").load(DIM_CLIENTE_PATH)

# 🔗 Junção entre vendas e dados do cliente para capturar região geográfica
df_vendas_local = (
    df_fato_vendas.join(df_dim_cliente, on="CustomerID", how="inner")
)

# 📊 Agregação por Estado e País com soma da receita
df_vendas_por_regiao = (
    df_vendas_local
    .groupBy("State", "Country")
    .agg(round(sum("TotalAmount"), 2).alias("TotalVendas"))  # 🎯 2 casas decimais
    .orderBy(desc("TotalVendas"))  # 🏆 Ordena por volume de vendas
)

# 📌 Exibe os estados mais lucrativos por país
df_vendas_por_regiao.display()


State Country TotalVendas RI Tonga 3.564967581E7 HI Faroe Islands 3.556084599E7 WI Brazil 3.33337563E7 FL San Marino 3.176591958E7 MN San Marino 3.110292987E7 ID Italy 3.041895357E7 MD Uzbekistan 2.810260614E7 NH Grenada 2.760457635E7 WY French Southern Territories 2.732721231E7 RI Myanmar 2.6962767E7 HI French Southern Territories 2.679618663E7 AL Belarus 2.627302617E7 MD United Kingdom 2.605719078E7 WY Palestinian Territory 2.584996146E7 MO Sri Lanka 2.560121724E7 MD Austria 2.559861786E7 PA Madagascar 2.41573752E7 CT Kenya 2.396094E7 SD Poland 2.395065834E7 IL Lithuania 2.371332795E7 MA Chad 2.368486575E7 VA Mauritania 2.368288785E7 GA Turkey 2.36310786E7 MA Saint Kitts and Nevis 2.355882903E7 ME Haiti 2.33358285E7 GA Andorra 2.332440753E7 PA Cameroon 2.285274108E7 AK Equatorial Guinea 2.253202464E7 NM Indonesia 2.234482074E7 IA Malta 2.23135923E7 CT Belgium 2.222276439E7 WA Switzerland 2.213406063E7 OH Cyprus 2.193973581E7 OH Cambodia 2.185862733E7 UT Colombia 2.185552737E7 WA Antigua and Barbuda 2.159326848E7 FL Slovenia 2.150403147E7 TX Guinea-Bissau 2.130252426E7 PA Saint Vincent and the Grenadines 2.122129569E7 MO France 2.1209067E7 WI Liberia 2.114883045E7 KY Burkina Faso 2.108022498E7 NJ Monaco 2.06997186E7 KY Luxembourg 2.063380842E7 OH Brazil 2.05915185E7 IL Singapore 2.021276271E7 NY Guadeloupe 2.021179878E7 UT France 2.02090707E7 ND Kyrgyz Republic 2.007373995E7 DC Guyana 1.991199687E7 NY Bahamas 1.985769603E7 SC Latvia 1.984714395E7 DC Guatemala 1.983023607E7 OH Anguilla 1.978028472E7 OK Albania 1.948801086E7 AK Bangladesh 1.936857624E7 IL Jamaica 1.917520176E7 IN Iceland 1.915881519E7 MS Tuvalu 1.906383585E7 MT Andorra 1.89775149E7 IA Senegal 1.887472305E7 IL Gibraltar 1.88331417E7 WV France 1.881190053E7 KS Botswana 1.876417542E7 WV Armenia 1.86513081E7 MO United Arab Emirates 1.856854395E7 MD Guernsey 1.852386279E7 SC Bermuda 1.851394401E7 MI Bhutan 1.843139778E7 AZ Egypt 1.840295322E7 WA Estonia 1.838334249E7 AZ Somalia 1.836772938E7 IL Slovakia (Slovak Republic) 1.832986206E7 KS Saint Pierre and Miquelon 1.820235852E7 IL Kazakhstan 1.801701E7 HI Falkland Islands (Malvinas) 1.796976216E7 VA Eritrea 1.793457786E7 CT Hong Kong 1.788377589E7 RI Albania 1.77336771E7 VA Mauritius 1.7733276E7 CA Aruba 1.761721272E7 AL Greenland 1.757444403E7 NY Tokelau 1.756256283E7 NJ Haiti 1.756184193E7 WY Ireland 1.751084541E7 AL Pakistan 1.74886695E7 VT Tanzania 1.748619057E7 CT Timor-Leste 1.745866521E7 NJ Malawi 1.744964115E7 PA Guam 1.742603913E7 NH Antigua and Barbuda 1.737859968E7 PA Cook Islands 1.734291741E7 MT Tokelau 1.710263808E7 WV Egypt 1.708281366E7 VT Martinique 1.70737479E7 PA Estonia 1.704070485E7 WV Samoa 1.703417001E7 WV Christmas Island 1.694844753E7 ID Cote d'Ivoire 1.68986562E7 IA Ecuador 1.679289471E7 KY Liberia 1.666409295E7 MN Mexico 1.665963942E7 SC United States of America 1.662080277E7 CO Ireland 1.654616124E7 IL Cook Islands 1.647901404E7 MT Russian Federation 1.644413139E7 MD New Caledonia 1.64435139E7 CA Guinea 1.643517018E7 TN Korea 1.636972281E7 OH Iraq 1.632706605E7 OK Serbia 1.627048254E7 KS Burundi 1.620989874E7 NV Northern Mariana Islands 1.612204011E7 WA Isle of Man 1.598031225E7 LA Samoa 1.595111553E7 WI Bulgaria 1.59389862E7 AZ Mexico 1.586693103E7 KS Martinique 1.58231511E7 GA Ukraine 1.580715564E7 ND Belize 1.578301605E7 PA Antarctica (the territory South of 60 deg S) 1.575942759E7 DC Jamaica 1.571564685E7 MO Turkmenistan 1.562998008E7 AL Cyprus 1.56216114E7 MT Guyana 1.554891735E7 MO Bermuda 1.539055677E7 WI Mozambique 1.534120155E7 CT Chad 1.52466876E7 PA Isle of Man 1.522914615E7 NV Oman 1.517827545E7 WA Micronesia 1.517041734E7 FL Kyrgyz Republic 1.51098516E7 WV Mongolia 1.499423328E7 RI Austria 1.498365108E7 SC Estonia 1.489941936E7 MT Burkina Faso 1.487990619E7 SD Portugal 1.474411533E7 NM Malta 1.473223053E7 MS Australia 1.459206849E7 MT Zambia 1.458077301E7 DC Palau 1.457857695E7 FL Guinea-Bissau 1.451487996E7 VA Finland 1.443132795E7 FL Holy See (Vatican City State) 1.436831256

# 🔄 Análise de Produtos com Maior Rotatividade por Período

## 🎯 Objetivo

Esta análise busca identificar **quais produtos apresentam maior rotatividade (mais vendidos)** ao longo do tempo, permitindo decisões mais precisas relacionadas a:

- **Previsão de demanda**
- **Gestão de estoque**
- **Negociação com fornecedores**
- **Campanhas promocionais e reposição inteligente**

## 📈 Aplicações da Análise

- Identificar **produtos-chave** para abastecimento contínuo
- Detectar variações sazonais de consumo
- Otimizar prateleiras e layout de lojas
- Apoiar decisões de compras corporativas

In [0]:
from pyspark.sql.functions import col, sum, round, desc, date_format
from pyspark.sql.window import Window

# 📁 Caminhos para as tabelas Delta
FATO_VENDAS_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_fato_vendas"
DIM_PRODUTO_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_dim_produto"

# 📥 Leitura das tabelas
df_fato_vendas = spark.read.format("delta").load(FATO_VENDAS_PATH)
df_dim_produto = spark.read.format("delta").load(DIM_PRODUTO_PATH)

# 🗓️ Extração do período (mês/ano) a partir da OrderDate
df_vendas_periodo = df_fato_vendas.withColumn("Periodo", date_format(col("OrderDate"), "yyyy-MM"))

# 🔗 Junção com a dimensão produto
df_vendas_produtos = df_vendas_periodo.join(df_dim_produto, on="ItemID", how="inner")

# 📊 Agregação: total de quantidade vendida por produto e por período
df_rotatividade_produto = (
    df_vendas_produtos
    .groupBy("Periodo", "ItemID", "ProductName")
    .agg(round(sum("Quantity"), 2).alias("TotalVendido"))
    .orderBy("Periodo", desc("TotalVendido"))
)

# 📌 Exibição do resultado
df_rotatividade_produto.display()


Periodo ItemID ProductName TotalVendido 2022-12 e0d8af68-58b8-40b6-a8fb-71a457047aef Monitor 9 2022-12 e4dbebe6-da6d-4c63-9c39-0478e517e69c Scanner 9 2022-12 49ce85ce-8307-4ad3-862d-dc2fab135c4e Monitor 9 2022-12 ec54b903-f07b-47aa-b132-f481662e8217 Motherboard 9 2022-12 8ec424d3-195f-4d07-8999-f1496c090eef Power Supply 9 2022-12 158b1eab-02e9-4a23-9016-84b9ff964fc3 Motherboard 9 2022-12 0822b96f-7ffc-4522-a01a-1199ce2771c0 USB Cable 9 2022-12 848ad90a-ea6f-4580-8d2c-491675438467 Laptop 9 2022-12 57ed5c74-c01e-4784-b646-a5b3ea8bb3d4 Graphics Card 9 2022-12 8c99fe6d-1e6e-413c-b96e-8d091a00255c Keyboard 9 2022-12 41f16aef-b850-42f5-9d86-17164c4d088d Printer 9 2022-12 98a26580-e157-43da-84f4-b357a717273e Smartphone 9 2022-12 747e7bcd-a860-49cb-899c-519f3d6fa256 Printer 9 2022-12 596fc69f-d53e-4a90-83c6-1a3cee542884 Printer 9 2022-12 dffd4724-4ddc-49ec-8623-de66265e7d31 Keyboard 9 2022-12 991c8d27-e4d4-464c-9e0e-6a3232b2f3f4 Monitor 9 2022-12 c92785a1-c621-486b-9a0c-e08839d653ff Power Supply 9 2022-12 caeb35bc-5024-4c01-ae32-1bf8e258b942 Smartwatch 9 2022-12 97694793-e80e-44fc-836f-bbdf3e126b58 Tablet 9 2022-12 38f0db55-b71c-41e3-9491-a252706e788b Smartwatch 9 2022-12 dc439f3d-6ae5-4b3e-a66b-cf620b4ff3ea Smartphone 9 2022-12 5e75f03e-3b98-4844-8730-9e7952a63b74 USB Cable 9 2022-12 2e4f0b5c-f416-4255-a196-c14780b9d404 Desk Lamp 9 2022-12 b40ecbae-9180-4432-886a-cfe0311ddb0b Laptop 9 2022-12 df0a1f35-1aa8-4666-bf88-9866ab9aabff Webcam 9 2022-12 7b03fbfd-b4bd-47e0-83eb-bc46540b2894 Keyboard 9 2022-12 03a77cc6-bff6-4566-9706-47eb03221f62 Scanner 9 2022-12 b64601e0-43cf-4d46-b04a-aace417c89ac Webcam 9 2022-12 c9c468c8-26b6-43b4-948f-bb8179cf5270 Webcam 9 2022-12 efc4c879-d24f-40c6-8328-ebf2e868e231 External Hard Drive 9 2022-12 fad46db2-b46b-4252-a7a5-28ecfef4ab78 Printer 9 2022-12 4a49c028-df89-4b50-a6d1-6e4360338382 Charger 9 2022-12 44edd07e-2247-4480-ac34-35ac9078fbf7 Gaming Chair 9 2022-12 ca8a728a-9663-45f0-a182-5b4e1b2581d9 Motherboard 9 2022-12 2c429421-1775-42a9-bbe2-133a66c60153 Headphones 9 2022-12 8e80944d-ac8b-4241-b8dd-c1cadd6322e1 Monitor 9 2022-12 a3d2f333-03ad-4a81-937f-0acbdba8de8e Router 9 2022-12 70590be5-f242-43cb-9441-8d1fb74a98d9 Smartwatch 9 2022-12 53a93a31-65dc-4380-906f-d62a7fefa250 Router 9 2022-12 45a83b85-7d26-446a-aa0b-e477d4a85340 Tablet 9 2022-12 8f12907b-13f0-4926-a941-bd1dbb5d1b46 Smartphone 9 2022-12 ce726302-c815-4a3a-9cb4-00c4861c6f2f Laptop 9 2022-12 1ed9c3b8-f5e0-440c-8676-b90f57a9c2d6 Smartphone 9 2022-12 2a2d7ac4-4aa0-4ff6-abf1-7d7059faca2c Router 9 2022-12 5f6e7b81-09cb-4847-9ac4-a0fec1984b0f Printer 9 2022-12 98fc2746-746f-423f-8d9c-71f319658cd1 Mouse 9 2022-12 4f627203-558f-4211-9e08-305492a23843 Smartwatch 9 2022-12 7df3ee4f-e1d7-4266-baea-f166c403c9f7 Scanner 9 2022-12 90978f06-215e-4402-aeb5-9b3b59b6ea6d Graphics Card 9 2022-12 d7c1c81a-c2c2-408b-a286-1e1a4f942d76 Monitor 9 2022-12 50bb3c30-257d-4945-9549-7709941cb6a2 Motherboard 9 2022-12 54c0de46-2dc6-4c35-940c-60fefc95d68e Printer 9 2022-12 ec0c9b76-28f3-482e-97d5-3ae54d19a17d Headphones 9 2022-12 c5393533-f7ed-4065-94b2-ad53c2de8718 Router 9 2022-12 f5aa167c-0a4a-42cf-8a01-615cccf0ee31 Graphics Card 9 2022-12 f0172e2e-b88e-4c86-b7ce-269923a4be6f USB Cable 9 2022-12 73b85fb9-1cf4-4b7f-b2d8-aebf20037bf1 Router 9 2022-12 631dc258-a6d2-4137-a808-3b88d78b324d Webcam 9 2022-12 994c0b62-9595-4624-aa3a-a0ad0c296cdf Laptop 9 2022-12 5aa5041e-6f29-4257-a107-b69a76908af6 Keyboard 9 2022-12 8c625de0-1cfe-4da9-b502-dc82c0595845 Gaming Chair 9 2022-12 56be58c5-74d6-4939-bba3-928cb1cd506c Headphones 9 2022-12 15490a93-311b-426a-af08-08ea03ac9ec3 Power Supply 9 2022-12 d3e9c7fc-95a8-4053-af27-1bc89b31d6e6 USB Cable 9 2022-12 84f8b477-56fe-4423-9c4a-1c0736fa1f47 Scanner 9 2022-12 b784fee3-5232-4a7c-aeaa-ac250180fe67 Tablet 9 2022-12 527ff8ce-713a-4c7a-85b3-a259805b312a Power Supply 9 2022-12 497a0701-8257-4393-a25b-74c994efc7d9 Gaming Chair 9 2022-12 e1818d98-1467-4b00-b54c-ff8da67ac207 Webcam 9 2022-12 746ef2ff-89ed-4857-bedc-e5ba59b32777 Graphics Ca

# 💰 Análise de Ticket Médio por Cliente e por Região com Ranking

## 🎯 Objetivo

Esta análise tem como finalidade identificar o **poder de compra dos clientes por região**, utilizando o ticket médio como métrica principal. O resultado ajuda a:

- 📍 Ajustar preços por localização
- 🎯 Direcionar campanhas segmentadas
- 🧠 Entender o comportamento do consumidor regionalmente
- 📦 Avaliar oportunidades de expansão

## 📈 Aplicações Práticas

- **Marketing**: campanhas focadas em regiões com maior poder aquisitivo
- **Comercial**: foco em regiões com ticket alto para novos produtos premium
- **Finanças**: avaliação do perfil de compra para precificação regional
- **Expansão**: seleção de locais com maior potencial de retorno

In [0]:
from pyspark.sql.functions import col, round, sum, countDistinct, avg, dense_rank
from pyspark.sql.window import Window
import pyspark.sql.functions as F

# 📁 Caminhos para as tabelas Delta
FATO_VENDAS_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_fato_vendas"
DIM_CLIENTE_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_dim_cliente"

# 📥 Leitura das tabelas
df_fato = spark.read.format("delta").load(FATO_VENDAS_PATH)
df_cliente = spark.read.format("delta").load(DIM_CLIENTE_PATH)

# 🔗 Junção entre fato_vendas e dim_cliente via CustomerID
df_joined = df_fato.join(df_cliente, on="CustomerID", how="inner")

# 🧮 Cálculo do ticket médio por cliente (TotalAmount / pedidos únicos)
df_ticket_cliente = (
    df_joined.groupBy("State", "Country", "CustomerID")
    .agg(round(sum("TotalAmount") / countDistinct("OrderID"), 2).alias("TicketMedioCliente"))
)

# 🧮 Cálculo do ticket médio por região
df_ticket_regiao = (
    df_ticket_cliente.groupBy("State", "Country")
    .agg(round(avg("TicketMedioCliente"), 2).alias("TicketMedioPorRegiao"))
)

# 🏅 Janela para ranking (do maior para o menor ticket médio)
windowSpec = Window.orderBy(F.desc("TicketMedioPorRegiao"))

# 🏆 Aplicando ranking
df_ranked = df_ticket_regiao.withColumn("Ranking", dense_rank().over(windowSpec))

# 📌 Exibição final ordenada pelo ranking
df_ranked.orderBy("Ranking").display()


State Country TicketMedioPorRegiao Ranking WI Brazil 1149439.87 1 ID Italy 1126627.91 2 AL Belarus 1050921.05 3 MD United Kingdom 1042287.63 4 AK Equatorial Guinea 1024182.94 5 IA Malta 1014254.2 6 WY French Southern Territories 1012118.97 7 WI Liberia 1007087.16 8 VA Mauritania 986786.99 9 NH Grenada 985877.73 10 MN San Marino 971966.56 11 RI Myanmar 962955.96 12 WY Palestinian Territory 957405.98 13 MA Chad 947394.63 14 RI Tonga 938149.36 15 ME Haiti 933433.14 16 PA Madagascar 929129.82 17 MN Mexico 925535.52 18 IL Jamaica 913104.85 19 IL Lithuania 912051.08 20 FL Slovenia 896001.31 21 CT Belgium 888910.58 22 TX Guinea-Bissau 887605.18 23 CT Kenya 887442.22 24 SD Poland 887061.42 25 MO Sri Lanka 882800.59 26 PA Cameroon 878951.58 27 GA Turkey 875225.13 28 OH Cambodia 874345.09 29 MA Saint Kitts and Nevis 872549.22 30 MS Tuvalu 866537.99 31 GA Andorra 863866.95 32 NJ Monaco 862488.27 33 DC Guatemala 862184.18 34 TN Korea 861564.36 35 VA Costa Rica 856020.17 36 IL Singapore 842198.45 37 UT Colombia 840597.21 38 AL Greenland 836878.29 39 NJ Malawi 830935.29 40 WA Antigua and Barbuda 830510.33 41 DC Guyana 829666.54 42 KS Saint Pierre and Miquelon 827379.93 43 SC Latvia 826964.33 44 IL Cook Islands 823950.7 45 IA Senegal 820640.13 46 HI Falkland Islands (Malvinas) 816807.37 47 KS Botswana 815833.71 48 CT Hong Kong 812898.9 49 ND Kyrgyz Republic 802949.6 50 AL Pakistan 794939.52 51 CT Timor-Leste 793575.69 52 WA Switzerland 790502.17 53 NH Antigua and Barbuda 789936.35 54 PA Antarctica (the territory South of 60 deg S) 787971.38 55 SC Liechtenstein 785643.03 56 OH Cyprus 783561.99 57 MD New Caledonia 783024.47 58 MO Turkmenistan 781499.0 59 KY Burkina Faso 780749.07 60 WV Armenia 777137.84 61 MD Guernsey 771827.62 62 RI Qatar 770952.83 63 MO Bermuda 769527.84 64 ID Cote d'Ivoire 768120.74 65 IN Iceland 766352.61 66 KY Luxembourg 764215.13 67 IL Slovakia (Slovak Republic) 763744.25 68 NY Tokelau 763589.69 69 OH Brazil 762648.83 70 WA Isle of Man 760967.25 71 LA Samoa 759576.93 72 PA Guam 757653.88 73 KS Martinique 753483.39 74 WV Mongolia 749711.66 75 OK Albania 749538.88 76 NY Guadeloupe 748585.14 77 AK Bangladesh 744945.24 78 WV Egypt 742731.03 79 PA Estonia 740900.21 80 MI Bhutan 737255.91 81 AZ Egypt 736118.13 82 NY Bahamas 735470.22 83 WA Estonia 735333.7 84 IL Hungary 734833.36 85 AZ Somalia 734709.18 86 NV Northern Mariana Islands 732820.01 87 PA Saint Vincent and the Grenadines 731768.82 88 OH Gibraltar 728670.35 89 IL Gibraltar 724351.6 90 SC United States of America 722643.6 91 UT France 721752.52 92 NM Indonesia 720800.67 93 ND Belize 717409.82 94 VA Eritrea 717383.11 95 DC Jamaica 714347.58 96 MO United Arab Emirates 714174.77 97 ME Saint Barthelemy 711481.96 98 WV Samoa 709757.08 99 RI Albania 709347.08 100 MT Burkina Faso 708566.96 101 OK Serbia 707412.28 102 MO France 706968.9 103 HI Faroe Islands 703813.8 104 NH Ireland 699429.55 105 DC Palau 694217.95 106 IL Kazakhstan 692961.92 107 PA Isle of Man 692233.92 108 MD Botswana 690289.92 109 WA Micronesia 689564.42 110 ME Tanzania 685833.47 111 SC Bermuda 685701.63 112 VT Martinique 682949.92 113 OH Anguilla 682078.78 114 VA Mauritius 682049.08 115 FL Brazil 680998.51 116 OH Iraq 680294.42 117 OR Gibraltar 678536.04 118 SC Monaco 675730.15 119 VT Tanzania 672545.79 120 SC Mauritania 669652.87 121 MI Wallis and Futuna 668855.42 122 IA Bouvet Island (Bouvetoya) 668310.85 123 PA Cook Islands 667035.29 124 WI Mozambique 667008.76 125 AZ Mexico 661122.13 126 DE Solomon Islands 658302.91 127 CA Guinea 657406.81 128 NC Malta 652972.09 129 CA Aruba 652489.36 130 MO Thailand 652065.43 131 ME Iceland 651891.48 132 WV Christmas Island 651863.37 133 RI Austria 651463.09 134 ND Canada 651006.36 135 AL Cyprus 650900.47 136 FL San Marino 649367.26 137 OH Tajikistan 648401.27 138 MT Guyana 647871.56 139 ME Faroe Islands 646822.76 140 IL Turks and Caicos Islands 645911.96 141 IA Ecuador 645880.57 142 TX Mozambique 644378.47 143 WA Reunion 643624.38 144 SD Portugal 641048.49 145 CT Moro

# 🚫 Análise de Produtos com Maior Número de Cancelamentos

## 📊 Objetivo
Identificar quais produtos apresentaram o maior número de **cancelamentos** de pedidos, a partir da análise da tabela `fato_vendas` integrada com a dimensão `dim_produto`.

Essa informação é **crucial para ações corretivas** com fornecedores, revisão de processos logísticos ou de qualidade e ajustes na comunicação com os clientes.

---

## 🧠 Justificativa de Negócio
Cancelamentos constantes podem indicar:

- Problemas de **qualidade do produto**
- Expectativas **não atendidas** do cliente
- Falhas de **logística ou entrega**
- **Problemas na descrição** do produto no site ou aplicativo

Agir sobre esses dados reduz custos, melhora a experiência do cliente e aumenta a eficiência operacional.

## 📌 Insights Possíveis

- **Foco corretivo imediato** nos produtos com maior cancelamento
- **Negociação com fornecedores** para produtos com alta taxa de devolução
- **Ajuste de campanhas** para evitar promoções de produtos problemáticos
- Suporte à **gestão de estoque e logística reversa**

In [0]:
from pyspark.sql.functions import col, count
from pyspark.sql import functions as F

# 📁 Caminhos das tabelas Delta
FATO_VENDAS_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_fato_vendas"
DIM_PRODUTO_PATH = "abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_dim_produto"

# 📥 Leitura das tabelas
df_fato = spark.read.format("delta").load(FATO_VENDAS_PATH)
df_produto = spark.read.format("delta").load(DIM_PRODUTO_PATH)

# 🎯 Filtrar registros com status "Cancelled"
df_cancelados = df_fato.filter(F.lower(col("Status")) == "cancelled")

# 🔗 Junção com a dimensão de produtos
df_joined = df_cancelados.join(df_produto, on="ItemID", how="inner")

# 📊 Agrupar por produto e contar cancelamentos
df_produto_cancelado = (
    df_joined.groupBy("ItemID", "ProductName")
    .agg(count("*").alias("TotalCancelamentos"))
    .orderBy(col("TotalCancelamentos").desc())
)

# 👀 Exibir resultado
df_produto_cancelado.display()


ItemID ProductName TotalCancelamentos 85ef2099-1273-4769-80e6-619081ff4a35 Graphics Card 3 41c0c8f4-13c0-46f6-8f3a-4498085800dc Smartwatch 3 f63cc6ca-4b8b-4502-ba3b-fa59fcbfad45 Printer 3 a41fb184-8006-4971-855b-2f083f7642f5 Headphones 3 856753d8-79bc-4279-84db-3155d761a2d6 Desk Lamp 3 a02f89f3-85ff-4e58-88eb-bf3a3001ee98 Keyboard 3 eff4fcd8-6cc5-4c42-b1e1-7653abf36378 Printer 3 3badb04a-6ca3-4f5a-867a-79805c775d6a Printer 3 7e5540f8-8b3d-4784-936f-92cb37d29e4e Graphics Card 3 0ec0480c-f9c8-4153-88b0-680bf12e8d2d Monitor 3 097d3910-777d-40b6-91f4-88e13ae6f628 Headphones 3 870e414e-6622-4cb2-a33b-fb1cf66d6bf1 Smartwatch 3 d4ba51fe-2cda-4d67-9453-dbe8aebce92a Motherboard 3 bbd8683a-bc49-4159-85f5-81c301c719ef Tablet 3 c81e2cb9-75b4-4dda-a7e0-c1afe539ecbd Smartwatch 3 aa9a7066-44db-4288-8629-ea692639f572 Printer 3 509de0a3-2d24-4800-8166-d86bd9bf6e78 Smartphone 3 456b944c-1776-47ce-9d38-0725aeaf0b54 USB Cable 3 cf829d9d-d115-421a-8f63-0629601634c5 Keyboard 3 bb6cfaa5-54bd-49c8-aa2d-2fe68401f544 Power Supply 3 6ee516c8-36f4-4ee3-9da8-77cb320b2a0c Laptop 3 f35b4fcc-1bb3-467d-8370-a6c57e0caa67 Router 3 a9c19fe5-0d68-484d-a8e9-1ef02f80c8b6 Power Supply 3 ae8cae24-2e90-4e78-8a4c-08f9739ca9b6 Keyboard 3 ba57b6e7-bc2e-4f99-8a3c-6df37828c7cd Scanner 3 0ddcea7d-d546-4ffa-ae70-cfc2cb029098 Gaming Chair 3 0b315ca7-a184-46c5-aefe-719f17cdca12 Printer 3 610fab7a-4517-4bc4-b558-5297448fb1c1 Laptop 3 c8618b14-773c-44b1-a27a-edb5b8707a5b Gaming Chair 3 1434b90b-5484-4da3-92a9-037ba47a4c3c Mouse 3 0234ca17-b9dd-42a4-a31d-41532eb52bb0 Smartphone 3 be8882fc-89bf-4bf0-a69c-b09ac6c25e62 Keyboard 3 3f903a83-e79f-44e5-a05c-deb607957c6e Mouse 3 3b9e5541-bccf-4f0e-a795-5cdbc66f1a9c Printer 3 c18063ab-0755-4856-9e02-3bb76ec07b2a Webcam 3 ab61ab95-e657-4d34-a318-9583e19084cf Power Supply 3 d6a052fb-61fa-487a-b9e7-89a5e5275fef Smartphone 3 88a961d3-ab9f-42f5-91da-3488dcbba950 Scanner 3 ce168cbc-a6f2-46db-85be-526c451d33b6 Router 3 e2b577f9-3741-430f-8036-5a82017a3ed4 Laptop 3 0cab796b-047f-4797-a452-d69035e5694b Smartwatch 3 1a68d900-ffe1-4bd1-a483-3ee035e31c8e Laptop 3 b71fa7d3-35eb-48d5-a5f5-26a3a4605796 Laptop 3 21fdb245-84ca-47e1-9d6b-4161a5f30cb0 Tablet 3 435898b5-6116-4d6b-89d9-66f3bd90c50f Webcam 3 72505518-ff60-426e-b900-e4035e9b4f6d Scanner 3 b7dcc27d-c0b9-48e4-a39c-bf9b80a42a81 Keyboard 3 938ebfb3-0e95-4047-a9c8-1b167035206a Motherboard 3 3425ea5b-2ba9-4118-ad9a-f549191d2d29 External Hard Drive 3 fa5b254f-c730-435e-a75e-47fa69f60586 USB Cable 3 ced77293-ea32-4ca9-a674-ed95a59a4f94 Graphics Card 3 0efbf23a-0bc0-44ef-bd50-71ac39c52471 Power Supply 3 8118414c-d28b-4543-bf8a-d4e6b77fbe3b Graphics Card 3 a1fe8dbd-52ec-4bfb-9058-c247c1a36f2c Desk Lamp 3 8edb73d7-7bce-4938-9d66-adb872b1b6bb Graphics Card 3 68dccf93-5c4d-486b-ba6c-5a781655d341 Charger 3 8833f300-f3df-44c1-a47b-4f930fea4656 Printer 3 891fce7d-1003-4b54-906e-1823bfa4ba57 Scanner 3 7b9e1124-b440-4dcd-be70-dab330112d25 Headphones 3 f531af62-aa39-45db-8d64-4912b030b584 Smartphone 3 45c483b2-bad6-48eb-ba95-e8a18a6a32df Desk Lamp 3 ae187e6b-bd29-4ee5-b2cd-723b3b471c9d Smartphone 3 cd9f9a21-eb57-4fb4-9fd3-f3c9af1caf7e Laptop 3 1a023f09-97a7-4849-b74e-c379edef103b Router 3 c3fa5802-d13d-4c4a-840d-14e4eb22e705 Scanner 3 5b867655-84cc-4356-a97b-f695832791c8 Power Supply 3 f30e4347-12ea-4df1-b71b-5adf33184c6b USB Cable 3 21752f60-e23f-486a-b100-652b3726cc3f Printer 3 12586c9a-5b60-47fd-93cd-2ec5c3c43bb8 Smartwatch 3 0cf4b0d7-2585-4bf9-8ccc-45ca656a8618 Motherboard 3 de4943f9-2bc2-4bba-8f18-9572558f9fd1 Router 3 d300833b-06cf-494c-97fc-ecf21cc39a7a Gaming Chair 3 a166e27d-d92e-4bca-8a59-243e636e451f Smartwatch 3 8272d66b-33e7-4bf5-a3c0-8b9cc00c0dbe Gaming Chair 3 80a044a6-6e43-4d9f-9a4d-65ff2ad93058 Charger 3 a8b773f8-7ee1-4c37-93e2-4a90fd6acf25 Desk Lamp 3 8e636407-e79b-4332-bc38-575f604f5384 Router 3 9296a8a4-ae28-4ccf-815c-91a2f1157d77 Tablet 3 0268e4a1-0d9a-4fa0-95fa-fe03858f1dec Keyboard 3 699f0184-c98f-4f07-ba0b-2bda9d982498 Scanner 3 4101ef89-f3ec-4b70-8702-5453c1b84e73 Desk Lamp 3 3805eec4-d59

# 🧑‍💼 Análise de Perfis de Clientes com Maior Volume de Compras

## 🎯 Objetivo
Identificar quais perfis de clientes — com base em **faixa etária (`Age`)**, **estado (`State`)** e **país (`Country`)** — são responsáveis pelo maior volume de compras da empresa.

Essa análise é essencial para **segmentar campanhas de marketing**, personalizar ofertas e entender o comportamento de compra de diferentes grupos demográficos e geográficos.

---

## 🧠 Justificativa de Negócio

Entender os perfis que mais compram permite:

- Criar **campanhas personalizadas** para públicos com alto poder de compra
- Fazer **ajustes regionais** de preços e promoções
- **Focar a expansão comercial** onde há maior retorno
- Desenvolver **ações de fidelização** mais assertivas

## 📈 Possíveis Insights

- Público de 30 a 40 anos em **grandes capitais** tem alto volume de compra
- O estado de **São Paulo (BR)** apresenta forte participação na receita
- Potencial para **expandir ações de marketing regional** e segmentar campanhas por faixa etária


In [0]:
from pyspark.sql.functions import col, round, sum as _sum, row_number
from pyspark.sql.window import Window

# 📥 Leitura das tabelas Gold
df_fato = spark.read.format("delta").load("abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_fato_vendas")
df_cliente = spark.read.format("delta").load("abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_dim_cliente")

# 🔗 Junção das tabelas pela chave CustomerID
df_joined = df_fato.join(df_cliente, on="CustomerID", how="inner")

# 📊 Agregação do volume total de compras por perfil
df_agrupado = (
    df_joined.groupBy("Age", "State", "Country")
    .agg(round(_sum("TotalAmount"), 2).alias("VolumeTotalCompras"))
)

# 🏆 Ranking por volume de compras
windowSpec = Window.orderBy(col("VolumeTotalCompras").desc())

df_ranked = (
    df_agrupado.withColumn("Ranking", row_number().over(windowSpec))
    .orderBy(col("Ranking"))
)

# 📋 Exibição do resultado
df_ranked.display()


Age State Country VolumeTotalCompras Ranking 56 RI Tonga 3.564967581E7 1 29 WI Brazil 3.33337563E7 2 59 MN San Marino 3.110292987E7 3 21 ID Italy 3.041895357E7 4 35 HI Faroe Islands 2.908656351E7 5 47 NH Grenada 2.760457635E7 6 36 WY French Southern Territories 2.732721231E7 7 45 RI Myanmar 2.6962767E7 8 66 AL Belarus 2.627302617E7 9 65 MD United Kingdom 2.605719078E7 10 69 WY Palestinian Territory 2.584996146E7 11 70 MO Sri Lanka 2.560121724E7 12 61 PA Madagascar 2.41573752E7 13 20 CT Kenya 2.396094E7 14 27 SD Poland 2.395065834E7 15 69 IL Lithuania 2.371332795E7 16 60 MA Chad 2.368486575E7 17 69 VA Mauritania 2.368288785E7 18 25 GA Turkey 2.36310786E7 19 55 MA Saint Kitts and Nevis 2.355882903E7 20 64 ME Haiti 2.33358285E7 21 47 GA Andorra 2.332440753E7 22 61 PA Cameroon 2.285274108E7 23 28 AK Equatorial Guinea 2.253202464E7 24 51 NM Indonesia 2.234482074E7 25 24 IA Malta 2.23135923E7 26 41 CT Belgium 2.222276439E7 27 21 WA Switzerland 2.213406063E7 28 20 OH Cyprus 2.193973581E7 29 51 OH Cambodia 2.185862733E7 30 62 UT Colombia 2.185552737E7 31 62 WA Antigua and Barbuda 2.159326848E7 32 23 FL Slovenia 2.150403147E7 33 65 TX Guinea-Bissau 2.130252426E7 34 34 PA Saint Vincent and the Grenadines 2.122129569E7 35 24 MO France 2.1209067E7 36 52 WI Liberia 2.114883045E7 37 54 KY Burkina Faso 2.108022498E7 38 39 NJ Monaco 2.06997186E7 39 69 KY Luxembourg 2.063380842E7 40 45 OH Brazil 2.05915185E7 41 20 IL Singapore 2.021276271E7 42 43 NY Guadeloupe 2.021179878E7 43 31 UT France 2.02090707E7 44 27 ND Kyrgyz Republic 2.007373995E7 45 30 MD Austria 1.992984246E7 46 32 DC Guyana 1.991199687E7 47 69 NY Bahamas 1.985769603E7 48 22 SC Latvia 1.984714395E7 49 63 DC Guatemala 1.983023607E7 50 40 OH Anguilla 1.978028472E7 51 61 OK Albania 1.948801086E7 52 32 AK Bangladesh 1.936857624E7 53 30 IL Jamaica 1.917520176E7 54 56 IN Iceland 1.915881519E7 55 58 MS Tuvalu 1.906383585E7 56 42 MT Andorra 1.89775149E7 57 48 IA Senegal 1.887472305E7 58 48 IL Gibraltar 1.88331417E7 59 55 KS Botswana 1.876417542E7 60 61 WV Armenia 1.86513081E7 61 22 MO United Arab Emirates 1.856854395E7 62 21 MD Guernsey 1.852386279E7 63 56 SC Bermuda 1.851394401E7 64 68 MI Bhutan 1.843139778E7 65 53 AZ Egypt 1.840295322E7 66 66 WA Estonia 1.838334249E7 67 69 AZ Somalia 1.836772938E7 68 67 IL Slovakia (Slovak Republic) 1.832986206E7 69 39 MD Uzbekistan 1.823099922E7 70 41 KS Saint Pierre and Miquelon 1.820235852E7 71 47 IL Kazakhstan 1.801701E7 72 39 HI Falkland Islands (Malvinas) 1.796976216E7 73 30 VA Eritrea 1.793457786E7 74 35 CT Hong Kong 1.788377589E7 75 67 RI Albania 1.77336771E7 76 66 VA Mauritius 1.7733276E7 77 24 CA Aruba 1.761721272E7 78 57 AL Greenland 1.757444403E7 79 66 NY Tokelau 1.756256283E7 80 53 NJ Haiti 1.756184193E7 81 30 WY Ireland 1.751084541E7 82 59 AL Pakistan 1.74886695E7 83 47 VT Tanzania 1.748619057E7 84 31 CT Timor-Leste 1.745866521E7 85 65 NJ Malawi 1.744964115E7 86 33 PA Guam 1.742603913E7 87 69 NH Antigua and Barbuda 1.737859968E7 88 63 PA Cook Islands 1.734291741E7 89 59 MT Tokelau 1.710263808E7 90 65 WV Egypt 1.708281366E7 91 27 VT Martinique 1.70737479E7 92 43 PA Estonia 1.704070485E7 93 69 WV Samoa 1.703417001E7 94 36 WV Christmas Island 1.694844753E7 95 55 ID Cote d'Ivoire 1.68986562E7 96 38 FL San Marino 1.685864313E7 97 35 IA Ecuador 1.679289471E7 98 22 KY Liberia 1.666409295E7 99 62 MN Mexico 1.665963942E7 100 28 SC United States of America 1.662080277E7 101 37 CO Ireland 1.654616124E7 102 45 IL Cook Islands 1.647901404E7 103 52 MT Russian Federation 1.644413139E7 104 51 MD New Caledonia 1.64435139E7 105 39 CA Guinea 1.643517018E7 106 30 TN Korea 1.636972281E7 107 61 OH Iraq 1.632706605E7 108 28 OK Serbia 1.627048254E7 109 65 KS Burundi 1.620989874E7 110 62 NV Northern Mariana Islands 1.612204011E7 111 34 WA Isle of Man 1.598031225E7 112 50 LA Samoa 1.595111553E7 113 66 WI Bulgaria 1.59389862E7 114 22 AZ Mexico 1.586693103E7 115 43 KS Martinique 1.58231511E7 116 20 GA Ukraine 1.580715564E7 117 42 ND Belize 1.578301605E7 118 51 PA Anta

# 📊 Análise de Participação no Faturamento por Produto

## 🎯 Objetivo

Identificar os produtos com **maior participação no faturamento total da empresa**, com base nas vendas consolidadas. Essa análise é essencial para:

- Reconhecer os **produtos mais rentáveis**;
- Otimizar o **mix de produtos**;
- Direcionar **ações de marketing e estoque**;
- Embasar **decisões estratégicas de negócios**

## 🧩 Possíveis Ações

- **Focar campanhas** nos produtos que mais faturam;
- **Reavaliar produtos com baixa participação**;
- Negociar com fornecedores dos produtos top de venda;
- Ajustar **previsões de estoque e logística**.

In [0]:
from pyspark.sql.functions import col, sum as _sum, round, desc
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number

# 📥 Leitura das tabelas Gold
df_fato = spark.read.format("delta").load("abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_fato_vendas")
df_produto = spark.read.format("delta").load("abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_dim_produto")

# 🔗 Junção entre fato_vendas e dim_produto via ItemID
df_joined = df_fato.join(df_produto, on="ItemID", how="inner")

# 💰 Agregação: faturamento total por produto
faturamento_produto = (
    df_joined.groupBy("ItemID", "ProductName")
    .agg(_sum("TotalAmount").alias("FaturamentoProduto"))
)

# 📊 Cálculo do faturamento total da empresa (valor único)
faturamento_total = faturamento_produto.agg(
    _sum("FaturamentoProduto").alias("FaturamentoTotal")
).collect()[0]["FaturamentoTotal"]

# 🧮 Cálculo da participação percentual + arredondamento de valores
df_participacao = faturamento_produto.select(
    "ItemID",
    "ProductName",
    round(col("FaturamentoProduto"), 2).alias("FaturamentoProduto"),
    round((col("FaturamentoProduto") / faturamento_total) * 100, 2).alias("ParticipacaoPercentual")
)

# 🏆 Ranking dos produtos com maior impacto no faturamento
windowSpec = Window.orderBy(desc("ParticipacaoPercentual"))

df_ranked = (
    df_participacao.withColumn("Ranking", row_number().over(windowSpec))
    .orderBy("Ranking")
)

# 📋 Exibir resultado final
df_ranked.display()


ItemID ProductName FaturamentoProduto ParticipacaoPercentual Ranking a02f89f3-85ff-4e58-88eb-bf3a3001ee98 Keyboard 2655.57 0.01 1 7e5540f8-8b3d-4784-936f-92cb37d29e4e Graphics Card 2650.92 0.01 2 75f8e38f-13f2-4b80-8e9f-39705f146fac Printer 2446.83 0.01 3 e54ddbb2-a96c-4aec-8099-a8a278e4326b Graphics Card 2835.87 0.01 4 f331f743-1fd6-4191-a42b-7e267e9a186f Monitor 2896.95 0.01 5 50e10b8f-737a-443c-8bce-7dfcf550c450 Keyboard 2622.9 0.01 6 3eaa14a0-390d-41ea-bde4-de4f39a9820f Desk Lamp 2840.85 0.01 7 c81e2cb9-75b4-4dda-a7e0-c1afe539ecbd Smartwatch 2553.12 0.01 8 7ef5b411-5f1f-4bf9-83b0-51ca5d38601f Webcam 2477.91 0.01 9 509de0a3-2d24-4800-8166-d86bd9bf6e78 Smartphone 2680.95 0.01 10 bb6cfaa5-54bd-49c8-aa2d-2fe68401f544 Power Supply 2425.68 0.01 11 6ee516c8-36f4-4ee3-9da8-77cb320b2a0c Laptop 2569.92 0.01 12 a9c19fe5-0d68-484d-a8e9-1ef02f80c8b6 Power Supply 2347.53 0.01 13 2abc6f5b-8e9a-4ded-9ccb-0c64730812f8 Power Supply 2657.4 0.01 14 7a5551d4-56b6-41a9-82bd-da37523b6f17 External Hard Drive 2763.24 0.01 15 ba57b6e7-bc2e-4f99-8a3c-6df37828c7cd Scanner 2939.37 0.01 16 895cdc25-67a4-4ee3-9b4a-b75bc68cd0e6 Laptop 2625.99 0.01 17 7734fe18-c926-4ce4-b36d-b574f3be955d Smartwatch 2704.71 0.01 18 0b315ca7-a184-46c5-aefe-719f17cdca12 Printer 2878.71 0.01 19 1434b90b-5484-4da3-92a9-037ba47a4c3c Mouse 2637.48 0.01 20 0dab9ea5-1f2b-4d02-86e2-c49f52b8697d Router 2526.57 0.01 21 be8882fc-89bf-4bf0-a69c-b09ac6c25e62 Keyboard 2726.52 0.01 22 b2b9bf04-9349-4083-9358-c71f50705643 Tablet 2469.63 0.01 23 7c40f50e-fafc-4717-a58c-9018d5650af2 Power Supply 2926.59 0.01 24 ce168cbc-a6f2-46db-85be-526c451d33b6 Router 2710.92 0.01 25 6a2ac82a-5e9c-4e1c-8794-e3d5dc23c84c Headphones 2604.75 0.01 26 72707e71-fd0c-483b-9aa1-aa408000c986 Printer 2497.26 0.01 27 c92785a1-c621-486b-9a0c-e08839d653ff Power Supply 2484.99 0.01 28 0cab796b-047f-4797-a452-d69035e5694b Smartwatch 2358.27 0.01 29 1a68d900-ffe1-4bd1-a483-3ee035e31c8e Laptop 2806.47 0.01 30 b71fa7d3-35eb-48d5-a5f5-26a3a4605796 Laptop 2351.79 0.01 31 d4aca9b3-c9a7-4db0-a81c-739903432215 Webcam 2868.84 0.01 32 63f5846d-b452-49d3-8659-5533a928977f Charger 2619.36 0.01 33 2b0d1069-7b17-4b39-8f31-5a86096b78fe Mouse 2478.27 0.01 34 e4a1181c-d84e-41a8-b9c5-298b539a4a7a Headphones 2921.64 0.01 35 2c7feeab-12c4-46a5-9db6-aec6df5af66a Desk Lamp 2835.87 0.01 36 599e578f-1d2f-4681-aa3c-f29c68da04e9 Desk Lamp 2385.3 0.01 37 3425ea5b-2ba9-4118-ad9a-f549191d2d29 External Hard Drive 2470.2 0.01 38 bbcb3f34-59b4-4e51-9798-071003527253 Router 2905.56 0.01 39 46fc5a5d-240a-43bf-9cf5-1e4c63564e0f Headphones 2324.94 0.01 40 9f776261-a0b1-4433-ac14-fcfc496b63a5 Scanner 2903.19 0.01 41 a1fe8dbd-52ec-4bfb-9058-c247c1a36f2c Desk Lamp 2644.38 0.01 42 98ec19b8-8917-470f-8019-af9d5c4d2092 USB Cable 2447.04 0.01 43 9ed11ec9-8de3-41a4-a6ff-22a72a1e5372 Power Supply 2473.71 0.01 44 17a18705-95bc-4c71-ab14-a121c60ca1e5 Webcam 2802.18 0.01 45 68dccf93-5c4d-486b-ba6c-5a781655d341 Charger 2676.09 0.01 46 8833f300-f3df-44c1-a47b-4f930fea4656 Printer 2583.21 0.01 47 77bfaafa-536a-483e-a461-40f295b2a3ad Power Supply 2591.01 0.01 48 aab06ef7-0ecc-4c96-a931-3ae06141dd57 Router 2666.43 0.01 49 cd9f9a21-eb57-4fb4-9fd3-f3c9af1caf7e Laptop 2911.68 0.01 50 e596fb48-3c42-4943-bace-dd09fed696bd Graphics Card 2288.04 0.01 51 e9fb7869-7be8-432a-a29a-715ce8de3fc2 External Hard Drive 2492.4 0.01 52 b9f61d15-b6fb-4e68-92c2-8c6ae9f1d329 Gaming Chair 2331.96 0.01 53 34f613c0-43c9-42ac-bc6a-45c34d155574 Smartphone 2883.0 0.01 54 0354c8e3-3365-4a9b-b375-6283a62cdcd4 Mouse 2766.06 0.01 55 de1c346b-fc98-49bf-b968-1f1641950fe8 Headphones 2463.45 0.01 56 91e17aa1-afd9-46f2-8aa1-f2b45b28a264 Desk Lamp 2523.24 0.01 57 341d06c2-a006-43a1-ae84-4d849efddee6 Power Supply 2741.37 0.01 58 8272d66b-33e7-4bf5-a3c0-8b9cc00c0dbe Gaming Chair 2919.27 0.01 59 d57ab9ef-6862-4659-a944-afbfb20ec425 Power Supply 2634.18 0.01 60 867c763e-7bc4-4d44-9f8b-e15ee7632328 Laptop 2747.79 0.01 61 f9659616-0350-4339-85f0-dad0d83bb1bd Mouse 2390.58 0.01 62 20e3417f-3d35-41d2-8f60-d9b6a015225

# 📦 Análise de Produtos com Alto Volume de Vendas e Baixa Receita

## 🎯 Objetivo

Identificar os produtos que, apesar de apresentarem **alto volume de vendas**, resultam em **baixa geração de receita**.

Essa análise é essencial para:

- Avaliar **rentabilidade real** por produto;
- Detectar possíveis **problemas de precificação**;
- Repensar campanhas promocionais ou políticas comerciais;
- Direcionar **negociações com fornecedores**

## 🧩 Possíveis Ações

- **Rever preço de venda** desses produtos;
- Avaliar se o custo de produção e logística compensa o volume;
- Testar **novas estratégias comerciais ou pacotes promocionais**;
- Identificar **produtos estratégicos para fidelização**, mesmo com margem menor.

In [0]:
from pyspark.sql.functions import col, sum as _sum, round, desc, asc
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number

# 📥 Leitura das tabelas Gold
df_fato = spark.read.format("delta").load("abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_fato_vendas")
df_produto = spark.read.format("delta").load("abfss://gold@dlsprojetofixo.dfs.core.windows.net/gold_dim_produto")

# 🔗 Junção entre fato_vendas e dim_produto via ItemID
df_joined = df_fato.join(df_produto, on="ItemID", how="inner")

# 🧮 Agregação: total vendido por produto
df_agg = (
    df_joined.groupBy("ItemID", "ProductName")
    .agg(
        _sum("Quantity").alias("TotalVendido"),
        _sum("TotalAmount").alias("ReceitaTotal")
    )
)

# 🎯 Arredondar valores de receita para 2 casas decimais
df_agg = df_agg.select(
    "ItemID",
    "ProductName",
    col("TotalVendido"),
    round(col("ReceitaTotal"), 2).alias("ReceitaTotal")
)

# 🧠 Lógica: produtos com alto volume mas baixa receita
# Ordenar por maior quantidade e menor receita
windowSpec = Window.orderBy(desc("TotalVendido"), asc("ReceitaTotal"))

df_ranked = (
    df_agg.withColumn("Ranking", row_number().over(windowSpec))
    .orderBy("Ranking")
)

# 📋 Exibir os principais produtos com esse comportamento
df_ranked.display()


ItemID ProductName TotalVendido ReceitaTotal Ranking ad092ac0-13a6-4d52-87ef-91e6f1a74f5b Router 9 30.33 1 38dfe920-1b60-4f18-8d23-a3b5609f0a48 Graphics Card 9 30.33 2 c5befeb0-8763-445c-a21b-2b0f736fb459 Charger 9 30.69 3 6bd0bb45-6e16-41ac-b905-e79a3c5e9361 Monitor 9 30.69 4 4e4dbbc5-5369-4d17-80a7-23b567e182e6 Router 9 31.11 5 6c92fbdc-3a20-4bfa-b565-7b57852308c5 Scanner 9 31.44 6 71ed8261-ab60-4642-ad32-e879e034aec1 Tablet 9 31.44 7 6d00aeeb-0f3b-4efa-92f0-0361f8e6c9ce Motherboard 9 31.44 8 03a75287-4fa8-4d25-af28-75aff3dc1d6e Keyboard 9 31.86 9 5de173db-2d28-4684-81ab-2507bdcd588c Gaming Chair 9 33.18 10 d4cfc568-36f8-4bcc-845e-c9b9b95abd58 Scanner 9 33.84 11 9444b527-634f-4179-8e40-36f974674388 Smartwatch 9 35.85 12 789f9da9-c98c-4913-9df9-2f96b0e66b6a Desk Lamp 9 35.85 13 66daf75d-0089-4544-915f-03a6f3cf7e5d Tablet 9 35.85 14 ad651caa-c5f2-4e8d-8141-6e942fa87f8d Gaming Chair 9 35.85 15 4ba8dba2-5839-48c1-b074-0c2531b319c6 Motherboard 9 35.91 16 449e1999-6af6-487d-850c-d00e44719a95 USB Cable 9 35.91 17 6a1b3f6a-c528-4da7-83d3-d7617d921fee Router 9 36.27 18 f6056602-8c29-4881-9742-122fa94220dd Desk Lamp 9 36.54 19 560ef442-6539-4d27-acfe-ec01eef4399e Gaming Chair 9 36.54 20 5cf98a3a-d0fb-4f13-b44d-bb1466ca90b1 Laptop 9 36.96 21 c4a851dd-9b56-4ec7-87df-b2a47bd79c7f Mouse 9 36.96 22 f74c8f72-58a2-47f6-afce-f57973d94587 Router 9 36.96 23 2b435081-573c-4114-900c-6ae06870728f External Hard Drive 9 36.99 24 49cacf86-e5b3-4217-8932-7333bc5fd4e4 Mouse 9 37.14 25 700cc73c-29dd-43ce-b97f-ba7cbcd8c775 Headphones 9 38.52 26 6dcc7e90-78e2-4e9d-9f01-32cba33e354c Router 9 38.52 27 ca8a728a-9663-45f0-a182-5b4e1b2581d9 Motherboard 9 38.7 28 3e0a0e6b-5ccf-4626-a560-a335418afd86 Router 9 38.76 29 3956b475-a929-415b-8995-a64d0a4fd20c Desk Lamp 9 38.76 30 205ac98c-1f1c-486f-922e-7ee2b6cbe9c4 Headphones 9 38.94 31 8c763b9e-cefb-4910-9700-68cd6fbd254c Motherboard 9 39.0 32 cf12826b-7cec-43b0-a82d-f4da453698e6 Charger 9 39.0 33 eb50acd5-44d8-4111-a7ee-2fa2a5e9cc26 Scanner 9 40.11 34 02727a05-b1f9-4e29-9406-a3c81599e058 External Hard Drive 9 40.11 35 e7b523ac-f65c-4334-910b-fe9d5ebd3cb4 Tablet 9 40.5 36 3bb4b8bc-6280-4acd-873c-3e6ab0233daf Smartwatch 9 40.5 37 7d03a319-7f29-4e97-84fa-5acc965441a7 Laptop 9 40.65 38 efd26fa5-ed05-4073-939b-27e4d93f66be Gaming Chair 9 40.65 39 9caed923-940e-4d77-8f98-99b80b71eae5 Laptop 9 40.65 40 66e639df-c939-4e02-b9e2-d20d7b54e9e5 Keyboard 9 41.94 41 dcf6cc01-db09-4147-ae92-9d387778d9d3 Webcam 9 42.6 42 29c104c3-9816-4684-9021-482379242cf5 Monitor 9 42.6 43 55115eb6-377d-4d82-b473-c206d53415e4 Webcam 9 42.6 44 fca92cc7-7fc9-4df1-b478-488f6336b63a Smartwatch 9 43.08 45 dc13844c-35a5-42c1-8c4d-f5abbf2e32ab External Hard Drive 9 43.92 46 49f98687-464d-4359-9e19-33e1097beaae Scanner 9 43.92 47 be7364b8-0120-4f08-b7f9-42105a58c70e Keyboard 9 43.92 48 880a381c-d530-4c5e-ae5e-1c6aed9dd679 Monitor 9 44.04 49 fb09441e-1f5a-46e8-a35d-90df8c67429d Printer 9 44.04 50 5e9b6663-2886-4705-a462-9af81a92b1dd Motherboard 9 44.04 51 d6a14674-fe05-470e-9eaf-4c05ff92f20b Power Supply 9 44.04 52 18be43d5-4eba-4ea4-9d82-dfe2fdb245df Graphics Card 9 44.16 53 e19ef35a-8502-4b73-ac3c-5885ad4a063d Gaming Chair 9 44.16 54 d82e1d64-1c56-402a-b296-257acee65fb6 Printer 9 44.55 55 330723c5-7798-441e-877f-c19884f4fcaf Scanner 9 44.91 56 2947c5e3-0588-4d6a-a820-4bf2700a321b Printer 9 45.0 57 b53834a7-6435-4a79-820a-c4d1801a1372 USB Cable 9 45.03 58 3fc3cb16-73c6-4861-a44c-7b81d08a9ca7 Desk Lamp 9 45.36 59 41900306-88d5-44a5-85c8-1efceba616bb Gaming Chair 9 45.42 60 4d3fab70-61ca-4474-b879-4917af6e1f5a Keyboard 9 45.72 61 78ae82b8-97eb-4260-a1f4-e7b48c6d5820 Laptop 9 46.53 62 d8e748f3-728a-4bef-afb3-fe1ab9917d23 Smartwatch 9 46.62 63 ac5ef2f1-c23d-4195-9279-9e5bac05f1f2 Smartwatch 9 46.62 64 c675153a-58bb-46c9-b432-7e111ddf3966 Mouse 9 47.28 65 07a38208-14b9-4d75-a510-14ba2fa20a27 Monitor 9 47.37 66 e28980ba-1845-4632-996e-347b9b57d566 Smartphone 9 47.97 67 23b7100a-efd3-4150-bc92-78ad65072840 Router 9 48.48 68 c5588756-d72a-4b95-9ece-1eb7ff05a56f